In [ ]:
!pip install importlib-metadata==3.2.0
!pip install spacy
!python -m spacy download en_core_web_sm
!pip install https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-2.3.1/en_core_web_sm-2.3.1.tar.gz!pip install PyPDF2
!pip install PyPDF2
!pip install pdfminer.six
!pip install PyMuPDF
!pip install tika
!pip install unidecode

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Attempting uninstall: importlib-metadata
    Found existing installation: importlib-metadata 6.2.0
    Uninstalling importlib-metadata-6.2.0:
      Successfully uninstalled importlib-metadata-6.2.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
markdown 3.4.3 requires importlib-metadata>=4.4; python_version < "3.10", but you have importlib-metadata 3.2.0 which is incompatible.
gym 0.25.2 requires importlib-metadata>=4.8.0; python_version < "3.10", but you have importlib-metadata 3.2.0 which is incompatible.
flask 2.2.3 requires importlib-metadata>=3.6.0; python_version < "3.10", but you have importlib-metadata 3.2.0 which is incompatible.
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
2023-04-13 11:27:03.24229

In [ ]:
import PyPDF2
import nltk
import os
import time
import re
import string
import spacy
import json
from tika import parser
import fitz
from operator import itemgetter
from bs4 import BeautifulSoup
from spacy.matcher import Matcher
import pandas as pd
from nltk.corpus import stopwords
from unidecode import unidecode


nltk.download('stopwords')
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('universal_tagset')
nltk.download('wordnet')
nltk.download('brown')
nltk.download('maxent_ne_chunker')
nltk.download('words')


from pdfminer.high_level import extract_text
from spacy.matcher import Matcher

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package universal_tagset to /root/nltk_data...
[nltk_data]   Unzipping taggers/universal_tagset.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package brown to /root/nltk_data...
[nltk_data]   Unzipping corpora/brown.zip.
[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping chunkers/maxent_ne_chunker.zip.
[nltk_data] Downloading package words to /root/nltk_data...
[nltk_data]   Unzipping corpora/words.zip.


In [ ]:
!rm -r '/content/extracted_data'
!rm -r '/content/text_resumes'
!rm -r '/content/json_data'
!rm -r '/content/headings'

In [ ]:
!mkdir '/content/text_resumes'
!mkdir '/content/extracted_data'
!mkdir '/content/json_data'
!mkdir '/content/headings'

In [ ]:
class ResumeInformationExtractor:
  def __init__(self, directory_path):
    self.directory = directory_path
    self.text_directory = '/content/text_resumes'
    self.block_directory = '/content/extracted_data'
    self.json_directory = '/content/json_data'
    self.headings_directory = '/content/headings'
    self.nlp = spacy.load('en_core_web_sm')
    self.education = [
            'BE','B.E.', 'B.E', 'BS', 'B.S', 
            'ME', 'M.E', 'M.E.', 'MS', 'M.S', 
            'BTECH', 'B.TECH', 'M.TECH', 'MTECH', 
            'SSC', 'HSC', 'CBSE', 'ICSE', 'X', 'XII'
        ]
    self.matcher = Matcher(self.nlp.vocab)
    self.total = []
    self.store_text()
    print("DONE")

  def fonts(self, doc, granularity=False):
    styles = {}
    font_counts = {}
    for page in doc:
      blocks = page.get_text("dict")["blocks"]
      for b in blocks:
          if b['type'] == 0:
              for l in b["lines"]:
                  for s in l["spans"]:
                      if granularity:
                          identifier = "{0}_{1}_{2}_{3}".format(s['size'], s['flags'], s['font'], s['color'])
                          styles[identifier] = {'size': s['size'], 'flags': s['flags'], 'font': s['font'],
                                                'color': s['color']}
                      else:
                          identifier = "{0}".format(s['size'])
                          styles[identifier] = {'size': s['size'], 'font': s['font']}

                      font_counts[identifier] = font_counts.get(identifier, 0) + 1  # count the fonts usage

    font_counts = sorted(font_counts.items(), key=itemgetter(1), reverse=True)

    if len(font_counts) < 1:
        raise ValueError("Zero discriminating fonts found!")

    return font_counts, styles

  def font_tags(self, font_counts, styles):
    p_style = styles[font_counts[0][0]]
    p_size = p_style['size']
    font_sizes = []
    for (font_size, count) in font_counts:
        font_sizes.append(float(font_size))
    font_sizes.sort(reverse=True)
    idx = 0
    size_tag = {}
    for size in font_sizes:
        idx += 1
        if size == p_size:
            idx = 0
            size_tag[size] = '<p>'
        if size > p_size:
            size_tag[size] = '<h{0}>'.format(idx)
        elif size < p_size:
            size_tag[size] = '<s{0}>'.format(idx)

    return size_tag

  def extract_name(self , resume_text):
    
    nlp = spacy.load("en_core_web_sm")
    doc = nlp(resume_text)
    names = [ent.text for ent in doc.ents if ent.label_ == "PERSON"]

    pattern = [{'POS': 'PROPN'}, {'POS': 'PROPN'}]
    self.matcher.add('NAME', [pattern])
    doc = self.nlp(resume_text)
    matches = self.matcher(doc)
    for match_id, start, end in matches:
        span = doc[start:end]
        if span.text in names:
          return span.text
        else:
          return None

  def headers_para(self, doc, size_tag):
    header_para = []
    first = True
    previous_s = {}

    for page in doc:
        blocks = page.get_text("dict")["blocks"]
        for b in blocks:
            if b['type'] == 0:
                block_string = ""
                for l in b["lines"]:
                    for s in l["spans"]:
                        if s['text'].strip():
                            if first:
                                previous_s = s
                                first = False
                                block_string = size_tag[s['size']] + s['text']
                            else:
                                if s['size'] == previous_s['size']:
                                    if block_string and all((c == "|") for c in block_string):
                                        block_string = size_tag[s['size']] + s['text']
                                    if block_string == "":
                                        block_string = size_tag[s['size']] + s['text']
                                    else:
                                        block_string += " " + s['text']
                                else:
                                    header_para.append(block_string)
                                    block_string = size_tag[s['size']] + s['text']
                                previous_s = s
                    block_string += "|"
                header_para.append(block_string)
    return header_para

  

  def get_headings(self, elements):
    resume_headings = ['Education', 'Experience', 'Projects', 'Skills', 'Certifications', 'Achievements', 'Positions of Responsibility', 'Technical Skills', 'Leadership/Extracurricular', 'Objectives', 'Professional Summary', 'Workshops/Trainings/Bootcamps', 'Languages', 'Interests', 'Organizations', 'Coding Profiles', 'Strengths', 'Awards', 'Leadership','Achievements and Awards','Programming','Technical Skills']
    headings_ = []
    for item in elements:
        if item.startswith(('<h1>', '<h2>')):
            headings_.append(item)
    headings = []
    for item in headings_:
        if '>' in item and len(item.split('>')) > 1:
            text = item.split('>')[1].split('|')[0].strip()
            headings.append(text)
    filtered_words = []
    for word in headings:
        word = ''.join(e for e in word if e.isalnum() or e in ['/', '\\', ' '])
        filtered_words.append(word)
    filtered_headings = [word for word in filtered_words if word.lower() in [heading.lower() for heading in resume_headings]]
    edu_present = False
    proj_present = False
    exp_present = False
    skil_present = False
    for word in filtered_headings:
      if 'edu' in word.lower():
          edu_present = True
      elif 'skil' in word.lower():
          skil_present = True
      elif 'proj' in word.lower():
          proj_present = True
      elif 'exp' in word.lower():
          exp_present = True
    if not edu_present:
      filtered_headings.append('education')
    if not skil_present:
      filtered_headings.append('skills')
    if not proj_present:
      filtered_headings.append('projects')
    if not exp_present:
      filtered_headings.append('experience')
    return filtered_headings


  def extract_education(self,text):
    STOPWORDS = set(stopwords.words('english'))
    nlp_text = self.nlp(text)

    # Sentence Tokenizer
    nlp_text = [sent.text.strip() for sent in nlp_text.sents]

    edu = {}
    # Extract education degree
    for index, text in enumerate(nlp_text):
      for tex in text.split():
        # Replace all special symbols
        tex = re.sub(r'[?|$|.|!|,]', r'', tex)
        if tex.upper() in self.education and tex not in STOPWORDS:
            if index + 1 < len(nlp_text):
                edu[tex] = text + nlp_text[index + 1]
            else:
                edu[tex] = text


    # Extract year
    education = []
    for key in edu.keys():
        year = re.search(re.compile(r'(((20|19)(\d{2})))'), edu[key])
        if year:
            education.append((key, ''.join(year[0])))
        else:
            education.append(key)
    return education


  def extract_mobile_number(self , text):
    phone = re.findall(re.compile(r'(?:(?:\+?([1-9]|[0-9][0-9]|[0-9][0-9][0-9])\s*(?:[.-]\s*)?)?(?:\(\s*([2-9]1[02-9]|[2-9][02-8]1|[2-9][02-8][02-9])\s*\)|([0-9][1-9]|[0-9]1[02-9]|[2-9][02-8]1|[2-9][02-8][02-9]))\s*(?:[.-]\s*)?)?([2-9]1[02-9]|[2-9][02-9]1|[2-9][02-9]{2})\s*(?:[.-]\s*)?([0-9]{4})(?:\s*(?:#|x\.?|ext\.?|extension)\s*(\d+))?'), text)
    
    if phone:
        number = ''.join(phone[0])
        if len(number) > 10:
            return '+' + number
        else:
            return number

  def extract_email(self , email):
    email = re.findall("([^@|\s]+@[^@]+\.[^@|\s]+)", email)
    if email:
        try:
            return email[0].split()[0].strip(';')
        except IndexError:
            return None

  def extract_data(self, text , headings):
    regex_patterns = {}
    for heading in headings:
        regex_patterns[heading] = re.compile(r'^' + heading, re.IGNORECASE)

    text_blocks = {}
    for heading in headings:
        text_blocks[heading] = ''

    current_heading = None
    i = 0

    for line in text.split('\n'):
        found_heading = False
        for heading, regex_pattern in regex_patterns.items():
            if regex_pattern.match(line):
                current_heading = heading
                found_heading = True
                break
        if found_heading:
            continue

        if current_heading is not None:
            text_blocks[current_heading] += line + '\n'
    return text_blocks
  
  def get_file_content(self, doc):
    result=""
    for page in doc:
        result += page.get_text()
    return unidecode(result)

  
  def store_text(self):
    print(self.directory)
    files = sorted(os.listdir(self.directory))

    for file in files:
      try:
        path = self.directory + '/' + file
        doc = fitz.open(path)
        text_data = self.get_file_content(doc)
        if not text_data:
          continue
        with open(self.text_directory + '/' + file.split('.')[0] + '.txt', 'w') as f:
            f.write(text_data)
        
        mobile_number = self.extract_mobile_number(text_data)
        email = self.extract_email(text_data)
        name = self.extract_name(text_data)
        degrees = self.extract_education(text_data)
        font_counts, styles = self.fonts(doc, granularity=False)
        size_tag = self.font_tags(font_counts, styles)
        elements = self.headers_para(doc, size_tag)
        headings = self.get_headings(elements)
        self.total.append(headings)
        with open(self.headings_directory + '/' + file.split('.')[0] + '.txt', 'w') as f:
            f.write(str(headings))
        
        text_blocks = self.extract_data(text_data , headings)
        new_text_blocks = {
            'name' : name,
            'email' : email,
            'mobile' : mobile_number,
            'degrees' : str(degrees)
        }

        final_blocks = new_text_blocks.copy()
        final_blocks.update(text_blocks)
        print(final_blocks)
        with open(self.block_directory + '/' + file.split('.')[0] + '.txt', 'w') as f:
            for heading, final_block in final_blocks.items():
              if final_block:
                f.write(heading.upper() + '\n')
                f.write(final_block + '-' * 50 + '\n')
        
        with open(self.json_directory + '/' + file.split('.')[0] + '.json', 'w') as f:
            non_empty_text_blocks = {key: value.replace('\n', '|') for key, value in final_blocks.items() if value and value != "[]"}
            json.dump(non_empty_text_blocks, f, indent=2)
        
        with open('total_headings.txt', 'w') as f:
          for item in self.total:
            f.write("%s\n" % item)
      except:
          print(f"Skipping file {file}: could not open as PDF")
          continue

    return




In [ ]:
start_time = time.time()
RESUME_DIRECTORY = '/content/drive/MyDrive/resume/type0'
ResumeInformationExtractor(RESUME_DIRECTORY)
end_time = time.time()
total_time = end_time - start_time
print(f"Total time taken for type0: {total_time:.2f} seconds")
!zip -r /content/json_data0.zip /content/json_data

/content/drive/MyDrive/resume/type0
{'name': 'Ishika Gupta', 'email': 'ishika.g2101@gmail.com', 'mobile': '7248718664', 'degrees': "[('BTech', '2020'), 'SSC']", 'education': '', 'skills': '* Languages : C(proficient), C++(proficient), Python(proficient), Java(Beginner)\n* Web Skills : HTML, CSS, JavaScript, ReactJs\n* Technical/Programistic Skills : Front End Developer (Beginner),UI/UX, Cloud Computing, Competitive\nCoding, Proficiency with Algorithms and Data Structures, Machine Learning(Beginner).\n* Database : MySQL\n', 'projects': '* Smart Traffic Light Scheduling in Smart City.\n* ACM Website for our college ACM Student Chapter.\nUsing Python:\n* Leetspeak\n* Monty Hall Problem\n* URL Shortener\n* Four in a Row (Game)\n* Downloads Folder Sorter\n* Calculator\nFIELDS OF INTEREST\n* Web Development, Machine Learning, Competitive Coding, Cloud Computing\nACCOMPLISHMENTS AND TRAININGS\n* Microsoft Certification Program 2021 - Microsoft Certified : Azure Fundamentals.\n* Microsoft Cert

In [ ]:
start_time = time.time()
RESUME_DIRECTORY = '/content/drive/MyDrive/resume/type1'
ResumeInformationExtractor(RESUME_DIRECTORY)
end_time = time.time()
total_time = end_time - start_time
print(f"Total time taken for type1: {total_time:.2f} seconds")
!zip -r /content/json_data1.zip /content/json_data

/content/drive/MyDrive/resume/type1
{'name': None, 'email': 'aparna.shrutijha@gmail.com', 'mobile': '963069010', 'degrees': "[('CBSE', '2019')]", 'Projects': '', 'Education': "Mentored over 10 students from class 11-12 about education and career guidance\nas a part of Delhi's Govt initiative\nManaged a  team of 5 people and contacted HRs of several companies to bring\nsponsors for our college's Technical fest\nDesh ke Mentor\nInnerve\n Nov 2021\nMentor\nSponsorship Associate \n", 'Experience': 'C++, python, Kotlin, XML, SQL\nAndroid development \nAndroid Studio, Firebase, Git, Github, VS Code, Google cloud Platform\nSparkAR, Canva, Inkscape\nLanguages\nTech Domain \n Developer Tools \n Other Applications\n', 'Skills': '', 'Certifications': 'Aparna Jha\n9630690101 | aparna.shrutijha@gmail.com |\nLinkedIn\nNew Delhi Public School\nCBSE Class 12\n* Percentage: 72.6\nDelhi, India\n2019\nCompleted 5 courses on different tech domains \nLearnt about Computer networking, Operating systems and 

In [ ]:
start_time = time.time()
RESUME_DIRECTORY = '/content/drive/MyDrive/resume/type2'
ResumeInformationExtractor(RESUME_DIRECTORY)
end_time = time.time()
total_time = end_time - start_time
print(f"Total time taken for type2: {total_time:.2f} seconds")
!zip -r /content/json_data2.zip /content/json_data

/content/drive/MyDrive/resume/type2
{'name': 'Shivani Ghodampalle', 'email': 'shivanighodampalle@gmail.com', 'mobile': '7829393799', 'degrees': '[]', 'EDUCATION': 'National Institute of Technology , Karnataka\n2020 - 2024\nB.Tech- Electrical and Electronics Engineering\nMangalore, Inida\ncgpa - 8.42/10.0\nShaheen Independent PU College\n2018 - 2020\nHigher Secondary\nBidar, India\nPCMB - Percentage - 91.5%\n', 'Technical Skills': 'Languages\nC, C++, Python, HTML, CSS, SQL\nFrameworks/Tools\nGit, VS code, MATLAB, Django\nInterests\nWeb development, Deep learning,Data Structures and Algorithms, OS\nSoft Skills\nTime Management, Teamwork, Communication, Problem Solving, Leadership\n', 'PROJECTS': "Self Driving Car Simulation  | Deep Q-learning in RL\noct 2021 - mar 2022\n* Built a Neural Network using Keras\n* Used pygame and pymunk to set up a simulation environment\n* Trained our model to avoid obstacles and self drive in the environment using NN and Deep Q-Learning in RL .\n* After tra

In [ ]:
!rm -r '/content/extracted_data'
!rm -r '/content/text_resumes'
!rm -r '/content/json_data'
!rm -r '/content/headings'

In [ ]:
!mkdir '/content/text_resumes'
!mkdir '/content/extracted_data'
!mkdir '/content/json_data'
!mkdir '/content/headings'

In [ ]:
start_time = time.time()
RESUME_DIRECTORY = '/content/drive/MyDrive/resume/type3'
ResumeInformationExtractor(RESUME_DIRECTORY)
end_time = time.time()
total_time = end_time - start_time
print(f"Total time taken for type3: {total_time:.2f} seconds")
!zip -r /content/json_data3.zip /content/json_data

/content/drive/MyDrive/resume/type3
{'name': None, 'email': 'vijaylatwal12@gmail.com', 'mobile': '+91879123265', 'degrees': "[('BTech', '2020')]", 'education': '', 'skills': '', 'projects': 'Library Management System - This project utilizes concept of\ninheritance in C++.\nE-Voting System - This project utilizes web development\ntechnologies such as HTML,CSS, Javascript, etc.\nCERTIFICATES-\nIntroduction to HTML 5- Coursera\nRobotic Process Automation- Automation Anywhere\nCybersecurity Essentials- CISCO\nIBM cloud essentials- IBM\nIntroduction to Cyber security- CISCO\nEXTRA CURRICULAR ACTIVITIES & ACHIEVEMENTS\nActive programmer on LeetCode\nCODE-CHAOS by IEEE student Branch GEHU\nANNUAL FEST- Chess competitions\nParticipation in Coding competitions organized by technical\nclubs of GEHU\nE D U C A T I O N\nB.Tech CSE\n2020-Present\nGRAPHIC ERA HILL UNIVERSITY,\nDEHRADUN, UTTARAKHAND\nIntermediate, Science\n2019-2020\nKENDRIYA VIDYALAYA,\nDEHRADUN,UTTARAKHAND\nhttps://www.linkedin.com

In [ ]:
!rm -r '/content/extracted_data'
!rm -r '/content/text_resumes'
!rm -r '/content/json_data'
!rm -r '/content/headings'

In [ ]:
!mkdir '/content/text_resumes'
!mkdir '/content/extracted_data'
!mkdir '/content/json_data'
!mkdir '/content/headings'

In [ ]:
start_time = time.time()
RESUME_DIRECTORY = '/content/drive/MyDrive/resume/type4'
ResumeInformationExtractor(RESUME_DIRECTORY)
end_time = time.time()
total_time = end_time - start_time
print(f"Total time taken for type4: {total_time:.2f} seconds")
!zip -r /content/json_data4.zip /content/json_data

/content/drive/MyDrive/resume/type4
{'name': 'Vishal Kumar', 'email': 'vishalmittal2234@gmail.com', 'mobile': None, 'degrees': "[('CBSE', '2020'), ('BE', '2020')]", 'Projects': 'QUOTES DAILY\nIn this by clicking on button various quote appear\n', 'Skills': 'Java\nJavaScript\nWeb Development\nData Structures\n', 'education': "College/school University/Board Degree/Standard Passing\nDate\nPercentage/Pointer\nMukat Public\nSchool\nCBSE\n12th\n2020\n91%\nCU\nCUPB\nBE\nPresent\nPersonal\nInformation\nDate Of Birth\n27-10-2002\nNationality\nIndia\nFather's Name\nSurnder Kumar\nMarital Status\nSingle\nGender\nMale\nLanguages Known\nHindi,English\nAddress\n48 Guru Arjun Dev Colony, Rajpura, Punjab, India\nI hereby declare that all above information is in correct with fact or truth up to my knowledge and I bear the\nresponsibilities for the correctness of the above mentioned particulars.\nDate : 05/11/2021\nVishal Kumar\n\n", 'experience': 'Sep 2021 - Oct 2021\nSales Intern at Eracost pvt ltd\n

In [ ]:
!rm -r '/content/extracted_data'
!rm -r '/content/text_resumes'
!rm -r '/content/json_data'
!rm -r '/content/headings'

In [ ]:
!mkdir '/content/text_resumes'
!mkdir '/content/extracted_data'
!mkdir '/content/json_data'
!mkdir '/content/headings'

In [ ]:
start_time = time.time()
RESUME_DIRECTORY = '/content/drive/MyDrive/resume/unknown'
ResumeInformationExtractor(RESUME_DIRECTORY)
end_time = time.time()
total_time = end_time - start_time
print(f"Total time taken for unknown: {total_time:.2f} seconds")
!zip -r /content/json_data_unknown.zip /content/json_data

/content/drive/MyDrive/resume/unknown
{'name': 'Harsh Singla', 'email': 'harshsingla_co20b4_13@dtu.ac.in', 'mobile': '+91817875516', 'degrees': "[('BTech', '2020'), ('CBSE', '2018')]", 'EDUCATION': "B.Tech (Computer\nEngineering)\n2020-2024\nDelhi Technological University (DTU)\n9.40 CGPA\n(Till 4th Semester)\nCBSE (Class XII)\n2020\nRukmini Devi Public School, Pitampura, Delhi\n86%\nCBSE (Class X)\n2018\nRukmini Devi Public School, Pitampura, Delhi\n91.6%\nACADEMIC PROJECTS\n*\nTwizzy | Link\nKotlin, Firebase\n*\nDesigned and developed a secure live-chat application using Google's Firebase APIs and Android SDK\n*\nImplemented user credential verification system using Firebase Authentication\n*\nIntegrated Firebase Realtime database that store user information and messages\nACADEMIC ACHIEVEMENTS AND AWARDS\n*\nSelected for Adobe Career Academy Program 2022\n*\nGoogle Kickstart 2022 - Round C: Global Rank: 455\n*\nGoogle Kickstart 2022 - Round A: Global Rank: 462\n*\nGoogle CodeJam 2022